In [4]:

import os
import dill
import numpy as np
import scipy
from scipy import io as sio
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchgan
from utili.misc.misc import Adjust_Accelerator_settings,Create_Dataset_Result_Folder,find_pad



In [ ]:
import Dataset.Germany_wishpers_mosaic_Dataset_RESAMPLE_Augument as Dataset
cfg=Dataset.cfg
DATrain=Dataset.DATrain

In [ ]:
#Interface 


GPU_NUM=0
Use_Target_Attention=False
Use_Dis_Attention=True
target_dataset_seed=41
target_dataset_seed_list=[41,50,61,70,81,90,101,200,301,400]
number_of_target_train_sampels=cfg['number_of_target_labeled_sampels']
models_initilization_seed_list=target_dataset_seed_list
Pre_train_models_path='/project/prasad/Germany for CARYA/Results/Germany_wishpers_MOSAIC/Exp_ull_S_model_Resample_Agument_Separable_conv/Germany_wishpers_MOSAIC_lists.pkl'
Exp_name="dummmm"
T_model_my=[]
EPOCH =cfg["EPOCH_DA"]
LRD=cfg["LRD"]
LRT=cfg["LRT"]
assert Pre_train_models_path is not None, "Pre_train_models_path cannot be None"
with open(Pre_train_models_path, 'rb') as f:
                S_model= dill.load(f)

for i in range(len( S_model)):
    Paths =Create_Dataset_Result_Folder(Dataset,Exp_name)
  
    target_dataset_seed=target_dataset_seed_list[i]
    source_dataset_seed=target_dataset_seed_list[i]
    models_initilization_seed = target_dataset_seed_list[i]
    devices_DA, num_workers_DA, accelerator_type_DA= Adjust_Accelerator_settings(GPU_NUM=GPU_NUM)[3:]
    S_cnn=S_model[i]
    T_cnn_my=DATrain(Dataset,keep_train=False,num_workers= num_workers_DA,Result_path=Paths[-1],Source_Datamodule=None,random_seed=models_initilization_seed_list[i],lightgin_log_path=Paths[1],Num_of_Target_train_samples=number_of_target_train_sampels,S_cnn=S_cnn,EPOCH=EPOCH,LRT=LRT,LRD=LRD,Exp_name=Exp_name,devices=devices_DA,accelerator=accelerator_type_DA,Use_Target_Attention=Use_Target_Attention,Use_Dis_Attention=Use_Dis_Attention,i=i)
    Best_DA_light_model=Dataset.Light_DAtrain.load_from_checkpoint(T_cnn_my[-2],Source_model=S_cnn,Target_model=T_cnn_my[0],Discr_model=T_cnn_my[1].D_cnn) 
    T_cnn_my=(Best_DA_light_model.T_cnn,' ')
    T_model_my.append(T_cnn_my)
    with open(os.path.join(Paths[0],Dataset.Dataset_name+"_lists.pkl"), 'wb') as f:
        dill.dump(S_model, f)
        dill.dump(T_model_my, f)

